In [2]:
!pip install -q torch gtts moviepy opencv-python accelerate git+https://github.com/huggingface/diffusers
!pip -q install diffusers["torch"] transformers
!pip -q install datasets

In [3]:
import torch
# from datasets import load_dataset
from transformers import (
    AutoModelForCausalLM, #for automatically loading pre trained model for casual language modelling
    AutoTokenizer, # automatically selecting corresponding valid tokenizer
    # BitsAndBytesConfig, # for quantization configurations
    # HfArgumentParser, #simplifies handling cmd line args for hugging face
    # TrainingArguments, # managing hyperparameters like learning rate, epochs, etc.
    pipeline, # easy-to-use interface for performing various NLP tasks, such as text generation, text classification, question answering, etc.
    # logging, # setting & managing logs. Useful for debug and tracking training.
)
from diffusers import StableDiffusionPipeline

2024-07-02 16:03:05.934665: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-07-02 16:03:05.934825: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-07-02 16:03:06.087345: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered


In [4]:
system_prompt = "You are a creative writer. Generate engaging short stories based on the provided prompts. Each story should have a clear beginning, middle, and end, and should be imaginative and well-written."
model_1 = "NousResearch/Llama-2-7b-chat-hf"
model_2 = "kulkarni-atharva/Llama-2-7b-storyteller-v2-finetune"
prompt = "A story about hare and the tortoise in 800 words and third person narration."

In [5]:
model = AutoModelForCausalLM.from_pretrained(model_2)
tokenizer = AutoTokenizer.from_pretrained(model_2, trust_remote_code=True)

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

/opt/conda/lib/python3.10/site-packages/torch/_utils.py:831: UserWarning: TypedStorage is deprecated. It will be removed in the future and UntypedStorage will be the only storage class. This should only matter to you if you are using storages directly.  To access UntypedStorage directly, use tensor.untyped_storage() instead of tensor.storage()
  return self.fget.__get__(instance, owner)()


In [6]:
text_pipe = pipeline(task="text-generation", model=model, tokenizer=tokenizer, max_length=1024, truncation = True)
result = text_pipe(f"<s> [INST] <<SYS>> \n {system_prompt} \n <</SYS>> \n \n {prompt} [/INST]")
generated_paragraph_1 = result[0]['generated_text']
print(generated_paragraph_1)
# print(type(generated_paragraph_1))

Truncation was not explicitly activated but `max_length` is provided a specific value, please use `truncation=True` to explicitly truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (GLUE-style) with the tokenizer you can select this strategy more precisely by providing a specific strategy to `truncation`.


<s> [INST] <<SYS>> 
 You are a creative writer. Generate engaging short stories based on the provided prompts. Each story should have a clear beginning, middle, and end, and should be imaginative and well-written. 
 <</SYS>> 
 
 A story about hare and the tortoise in 800 words and third person narration. [/INST] `` Come on, come on, '' the hare urged the tortoise. The hare was impatient, and he wanted to get started on his race. He had heard about the tortoise's reputation, and he wasn't going to let him win. <newline> <newline> The tortoise looked at the hare, and he grinned. He wasn't going to let the hare win either. He had been training for months, and he was ready to show off his skills. <newline> <newline> The hare and the tortoise stood at the starting line, and they waited for the signal to begin. When the signal was given, they started running. <newline> <newline> The hare was off like a shot, and he was quickly in the lead. He was fast, and he was confident. He was going to w

In [7]:
import gc
del model
del tokenizer

gc.collect()
gc.collect()

0

In [8]:
# Sample paragraph as a string
# paragraph = "This is a sample paragraph. [INST]This text should be removed.[/INST] Here is more text. Another [INST]unwanted text here[/INST] to be removed."

# Find the starting and ending indices of the tags
start_tag = "[INST]"
end_tag = "[/INST]"

# Find all occurrences of the tags
start_index = generated_paragraph_1.find(start_tag)
end_index = generated_paragraph_1.find(end_tag)

# Continue removing all instances of the text between the tags until none are found
# while start_index != -1 and end_index != -1:
    # Remove the text between start_tag and end_tag including the tags themselves
paragraph = generated_paragraph_1[:start_index] + generated_paragraph_1[end_index + len(end_tag):]
    
    # Find the next occurrence of the tags
#     start_index = paragraph.find(start_tag)
#     end_index = paragraph.find(end_tag)

# Print the cleaned paragraph

generated_paragraph = paragraph.replace("<newline>", "")
generated_paragraph = generated_paragraph.replace("<s>", "")
print(generated_paragraph)
len(generated_paragraph)
generated_prompts = generated_paragraph.split('.')

  `` Come on, come on, '' the hare urged the tortoise. The hare was impatient, and he wanted to get started on his race. He had heard about the tortoise's reputation, and he wasn't going to let him win.   The tortoise looked at the hare, and he grinned. He wasn't going to let the hare win either. He had been training for months, and he was ready to show off his skills.   The hare and the tortoise stood at the starting line, and they waited for the signal to begin. When the signal was given, they started running.   The hare was off like a shot, and he was quickly in the lead. He was fast, and he was confident. He was going to win this race, and he knew it.   The tortoise was slower, but he was steady. He was determined to win, and he was going to do it. He was going to show the hare that he wasn't to be underestimated.   The hare and the tortoise ran and ran, and they were neck and neck. The hare was getting tired, and the tortoise was getting faster.   The hare looked back, and he saw 

In [9]:
print(len(generated_prompts))

36


In [ ]:
# import re

# # Define the regex pattern to match text between [INST] and [/INST]
# pattern = r'\[INST\].*?\[\/INST\]'

# # Remove the matched text
# cleaned_paragraph = re.sub(pattern, '', generated_paragraph_1)
# cleaned_paragraph.replace("<s>", "")
# # Print the result
# print(cleaned_paragraph)


In [10]:
pipe = StableDiffusionPipeline.from_pretrained("runwayml/stable-diffusion-v1-5", torch_dtype=torch.float16)
# redstonehero/cetusmix_v4

model_index.json:   0%|          | 0.00/541 [00:00<?, ?B/s]

Fetching 15 files:   0%|          | 0/15 [00:00<?, ?it/s]

model.safetensors:   0%|          | 0.00/1.22G [00:00<?, ?B/s]

(…)ature_extractor/preprocessor_config.json:   0%|          | 0.00/342 [00:00<?, ?B/s]

tokenizer/special_tokens_map.json:   0%|          | 0.00/472 [00:00<?, ?B/s]

...

tokenizer/vocab.json:   0%|          | 0.00/1.06M [00:00<?, ?B/s]

unet/config.json:   0%|          | 0.00/743 [00:00<?, ?B/s]

vae/config.json:   0%|          | 0.00/547 [00:00<?, ?B/s]

diffusion_pytorch_model.safetensors:   0%|          | 0.00/335M [00:00<?, ?B/s]

Loading pipeline components...:   0%|          | 0/7 [00:00<?, ?it/s]

In [13]:
pipe = pipe.to("cuda")
pipe.safety_checker = None

In [14]:
import os
from gtts import gTTS
from moviepy.editor import VideoClip, ImageClip, AudioClip, vfx, concatenate_videoclips, concatenate_audioclips, CompositeAudioClip
import cv2
# from mutagen.wave import WAVE
import shutil

In [15]:
for i in range(1,len(generated_prompts)):
    generated_prompts[i] = generated_prompts[0] + generated_prompts [i]
generated_images = []
# from diffusers import StableDiffusionPipeline
# pipe = StableDiffusionPipeline.from_pretrained("redstonehero/cetusmix_v4", torch_dtype=torch.float16)
# pipe = pipe.to("cuda")
# pipe.safety_checker = None
h=512
w=512
steps=50
guidance=7.5
neg = "easynegative, lowres, bad anatomy, bad hands, text, error, missing fingers, extra digit, fewer digits, cropped, worstquality, low quality, normal quality, jpegartifacts, signature, watermark, username, blurry, bad feet, cropped, poorly drawn hands, poorly drawn face, mutation, deformed, worst quality, low quality, normal quality, jpeg artifacts, signature, watermark, extra fingers, fewer digits, extra limbs, extra arms,extra legs, malformed limbs, fused fingers, too many fingers, long neck, cross-eyed,mutated hands, polar lowres, bad body, bad proportions, gross proportions, text, error, missing fingers, missing arms, missing legs, extra digit, extra arms, extra leg, extra foot,"
output_directory = "./images/"
os.makedirs(output_directory)
for i, prompt in enumerate(generated_prompts):
  prompt += "8K, ultradetailed"
  image = pipe(prompt, height=h, width=w, num_inference_steps=steps, guidance_scale=guidance, negative_prompt=neg).images[0]
  filename = os.path.join(output_directory , f"image_{i}.jpg")
  image.save(filename)
  generated_images.append(filename)

  0%|          | 0/50 [00:00<?, ?it/s]

  0%|          | 0/50 [00:00<?, ?it/s]

  0%|          | 0/50 [00:00<?, ?it/s]

  0%|          | 0/50 [00:00<?, ?it/s]

  0%|          | 0/50 [00:00<?, ?it/s]

...

  0%|          | 0/50 [00:00<?, ?it/s]

  0%|          | 0/50 [00:00<?, ?it/s]

  0%|          | 0/50 [00:00<?, ?it/s]

  0%|          | 0/50 [00:00<?, ?it/s]

  0%|          | 0/50 [00:00<?, ?it/s]

In [16]:
import gc
del pipe
gc.collect()
gc.collect()

0

In [33]:
from pydub import AudioSegment
audio_clips = []
audio_lengths = []
language="en"
# j = 1
# generated_paragraph = generated_paragraph.split('.')
output_directory = "./audio_files/"

# Create the directory if it doesn't exist
if not os.path.exists(output_directory):
    os.makedirs(output_directory)
generated_prompts = generated_paragraph.split('.')
for i, sentence in enumerate(generated_prompts):
    sentence = sentence.strip()
    speech = gTTS(text=sentence, lang=language, slow=False, tld="com.au")
    filename = os.path.join(output_directory, f"speech_{i}.mp3")
    speech.save(filename)
    audio_clips.append(filename)
    # Load the audio file
    audio_file = AudioSegment.from_file(filename)
    # Get the length of the audio in milliseconds
    audio_length_ms = len(audio_file)
    # Convert milliseconds to seconds
    audio_length_sec = audio_length_ms / 1000
#     audio = WAVE(filename)
#     audio_info = audio.info
#     length = int(audio_info.length)
    audio_lengths.append(audio_length_sec)
#     print(audio_length_sec)

In [ ]:


# for sentence in generated_paragraph:
#     speech = gTTS(text=sentence,lang=language,slow=False,tld="com.au")
#     audio_clips.append(speech)
    # audio = WAVE(speech)
    # contains all the metadata about the wavpack file
    # audio_info = audio.info
    # length = int(audio_info.length)
    # audio_lengths.append(length)
    # speech.save(f"audio{j}.mp3")
    # j+=1

In [ ]:
# /kaggle/working/audio_files

In [24]:
from moviepy.editor import AudioFileClip

In [34]:
video_clips = []
audio_clips_r = []
for i, image in enumerate(generated_images):
    clip = ImageClip(image).set_duration(audio_lengths[i])
    video_clips.append(clip)
for path in audio_clips:
  path = "/kaggle/working" + path[1:] 
  print(path)
  clip = AudioFileClip(path)
  audio_clips_r.append(clip)
final_video = concatenate_videoclips(video_clips)
final_audio = concatenate_audioclips(audio_clips_r)
final_video.audio = CompositeAudioClip([final_audio])
os.makedirs("./video/", exist_ok = True)
final_video.write_videofile("./video/final_video.mp4", fps = 24)

/kaggle/working/audio_files/speech_0.mp3
/kaggle/working/audio_files/speech_1.mp3
/kaggle/working/audio_files/speech_2.mp3
/kaggle/working/audio_files/speech_3.mp3
/kaggle/working/audio_files/speech_4.mp3
/kaggle/working/audio_files/speech_5.mp3
/kaggle/working/audio_files/speech_6.mp3
/kaggle/working/audio_files/speech_7.mp3
/kaggle/working/audio_files/speech_8.mp3
/kaggle/working/audio_files/speech_9.mp3
/kaggle/working/audio_files/speech_10.mp3
/kaggle/working/audio_files/speech_11.mp3
/kaggle/working/audio_files/speech_12.mp3
/kaggle/working/audio_files/speech_13.mp3
/kaggle/working/audio_files/speech_14.mp3
/kaggle/working/audio_files/speech_15.mp3
/kaggle/working/audio_files/speech_16.mp3
/kaggle/working/audio_files/speech_17.mp3
/kaggle/working/audio_files/speech_18.mp3
/kaggle/working/audio_files/speech_19.mp3
/kaggle/working/audio_files/speech_20.mp3
/kaggle/working/audio_files/speech_21.mp3
/kaggle/working/audio_files/speech_22.mp3
/kaggle/working/audio_files/speech_23.mp3
/k

MoviePy - Done.
Moviepy - Writing video ./video/final_video.mp4



Moviepy - Done !
Moviepy - video ready ./video/final_video.mp4


In [35]:
from IPython.display import Video, display
display(Video("/kaggle/working/video/final_video.mp4", embed=True))

In [ ]:
def delete_folder(folder_path):
    try:
        shutil.rmtree(folder_path)
        print(f"Deleted folder: {folder_path}")
    except Exception as e:
        print(f"Failed to delete folder: {folder_path}. Error: {e}")


# Danger Zone:

Running the following cells will delete the output files including the video generated.

In [ ]:
folder_path = ["/kaggle/working/audio_files", "/kaggle/working/images", "/kaggle/working/video"]
for path in folder_path:
    delete_folder(path)

In [ ]:
# delete_folder("/kaggle/working/audio_files")